In [1]:
import pandas as pd
import numpy as np
import bokeh as bk
import copy
import urllib
import statsmodels.api as sm
from statsmodels.stats.outliers_influence import summary_table

from bokeh.charts import Bar, Scatter, Line, output_file, show, HeatMap, Histogram
from bokeh.charts.attributes import ColorAttr, CatAttr
from bokeh.plotting  import figure, output_notebook
from bokeh.models import (HoverTool, 
                          ColumnDataSource, 
                          LinearColorMapper,
                          LinearAxis,
                          CustomJS,
                          ColorBar,
                          Range1d,
                          Label,
                          Span)


                          
from bokeh.palettes import Viridis6, Viridis256, RdYlGn10
from bokeh.models.widgets import Slider
from bokeh.layouts import column, row
output_notebook(hide_banner=True)

import map_helper as mh


import warnings
warnings.filterwarnings('ignore')
pd.options.display.max_columns = 60

#import seaborn as sns
#import matplotlib.pyplot as plt

from IPython.lib.display import FileLink

TOOLS = "pan,wheel_zoom,box_zoom,reset,save"

%load_ext autoreload
%autoreload 2


## Helper Functions for maps

In [2]:
#DFT_PTH = '/Users/Tinmar/Documents/Dev/Jupyter_nbs/hydrologic_regions_vs_counties.csv'
#DFT_PTH = 'https://s3-us-west-1.amazonaws.com/tdidataset/TDI/hydrologic_regions_vs_counties.csv'


In [3]:
DFT_PTH = './Data/hydrologic_regions_vs_counties.csv'

def simple_county_map(dfm,key='Production',width=600,height=600,palette=Viridis256,
                      state='ca',
                      title='California Production',
                      tools="pan,wheel_zoom,box_zoom,reset,hover,save",color_range=[]):
    from bokeh.sampledata.us_counties import data as counties
    palette = palette[::-1]

    counties = {
        code: county for code, county in counties.items() if county["state"] == state
    }

    county_xs = [county["lons"] for county in counties.values()]
    county_ys = [county["lats"] for county in counties.values()]

    county_names = [county['name'] for county in counties.values()]
    #county_rates = [unemployment[county_id] for county_id in counties]
    county_rates = [dfm[dfm['County'] == county['name']][key] for county in counties.values()]
    
    if not color_range:
        color_mapper = LinearColorMapper(palette=palette,low=dfm[key].min(),high=dfm[key].max())
    else:
        color_mapper = LinearColorMapper(palette=palette,low=color_range[0],high=color_range[1])

    source = ColumnDataSource(data=dict(
        x=county_xs,
        y=county_ys,
        name=county_names,
        rate=county_rates,
        ))

    p = figure(title=title, tools=tools,
               x_axis_location=None, y_axis_location=None,
               width = width, height = height)
    p.grid.grid_line_color = None

    p.patches('x', 'y', source=source,
              fill_color={'field': 'rate', 'transform': color_mapper},
              fill_alpha=0.7, line_color="white", line_width=0.5)

    hover = p.select_one(HoverTool)
    hover.point_policy = "follow_mouse"
    hover.tooltips = [
        ("County", "@name"),
        ("{}".format(key), "@rate"),

    ]
    color_bar = ColorBar(color_mapper=color_mapper, location=(0, 0), orientation='vertical')
    p.add_layout(color_bar, 'right')
    p.toolbar_location = 'left'
    return p


def process_stats_by_counties(dfm,key='GPCD',groupkey='Year',aggfunc='mean',srcpath=DFT_PTH):
    
    # Initialize dataframe of regions and counties
    
    region_counties_df = pd.read_csv(DFT_PTH)
    region_counties_df = region_counties_df[['Hydrologic Region','County']]

    list_df = []
    for elt in dfm[groupkey].unique():
        temp_df = copy.deepcopy(region_counties_df)
        temp_df[groupkey] = elt
        list_df.append(temp_df)

    # Overwrite initial dataframe
    region_counties_df = pd.concat(list_df)

    grouped_df = dfm.groupby(['Hydrologic Region','County',groupkey])[[key]].agg(aggfunc).reset_index()

    # Adding missing groups if present
    grouped_df = grouped_df.merge(region_counties_df,on=['Hydrologic Region','County',groupkey],how='outer')

    # If counties are missing in some groups fill In Average of hydrologic region
    grouped_df[key] = grouped_df.groupby(['Hydrologic Region',groupkey]).transform(lambda x: x.fillna(x.mean()))
    return grouped_df.groupby(['County',groupkey])[key].agg(aggfunc).reset_index()
    

def add_location_to_dfm(dfm,state="ca"):
    """ Given dataframe with County field adds county boundaries in order to 
    be used in the plotting routine  """
    # Build County boundary DataFrame from bokeh county data
    from bokeh.sampledata.us_counties import data as counties
    counties = {
                code: county for code, county in counties.items() if county["state"] == state
               }
    county_xs = [county["lons"] for county in counties.values()]
    county_ys = [county["lats"] for county in counties.values()]
    county_names = [county['name'] for county in counties.values()]
    
    location_df = pd.DataFrame({'County':county_names,'x':county_xs,'y':county_ys})
    return dfm.merge(location_df,on='County',how='left')


def interactive_county_map(dfm,key='GPCD',slider_key='Year',initial_query='Year == 2014',
                    title='California GPCD',tools = "pan,wheel_zoom,box_zoom,reset,hover,save", 
                    width=600,height=600,zscale='linear'):
    """ Plots interactive map given dataframe with COunty boundary fields as wall as 
    key value and slider_key present in columns"""
    palette = Viridis256
    palette = palette[::-1]

    if zscale == 'log':
        color_mapper = LogColorMapper(palette=palette,low=dfm[key].min(),high=dfm[key].max())
    else:
        color_mapper = LinearColorMapper(palette=palette,low=dfm[key].min(),high=dfm[key].max())

    source = ColumnDataSource(dfm.dropna(), id='src')
    source_flt = ColumnDataSource(dfm.query(initial_query).fillna(-1), id='src_flt')

    p = figure(title=title, tools=tools,x_axis_location=None, y_axis_location=None,
               width = width, height=height)
    p.grid.grid_line_color = None

    p.patches('x', 'y', source=source_flt,
              fill_color={'field': key, 'transform': color_mapper},
              fill_alpha=0.7, line_color="white", line_width=0.5)

    hover = p.select_one(HoverTool)
    hover.point_policy = "follow_mouse"
    hover.tooltips = [
        ("County", "@County"),
        ("{}".format(key), "@{}".format(key)),
        ]



    callback_js_code="""
                     var orig_data = s1.data;
                     var filtered_data = s2.data;
                     var selected = cb_obj["value"];

                     for (var key in orig_data) {{
                         filtered_data[key] = [];
                         for (var i = 0; i < orig_data['County'].length; ++i) {{
                             if (orig_data['{VARNAME}'][i] === selected)  {{
                                 filtered_data[key].push(orig_data[key][i]);
                             }}
                          }}
                     }}
                     s2.trigger("change");
                     """.format(VARNAME = slider_key)

    callback = CustomJS(args=dict(s1=source,s2=source_flt), code=callback_js_code)


    slider = Slider(start=dfm[slider_key].min(), 
                    end=avg_gp[slider_key].max(), 
                    value=avg_gp[slider_key].min(), step=1, 
                    title="Select {}".format(slider_key), width=width,
                    callback=callback)


    color_bar = ColorBar(color_mapper=color_mapper, location=(0, 0), orientation='vertical')
    p.add_layout(color_bar, 'right')
    p.toolbar_location = 'left'
    return column(slider,p)


## Why is that interesting? 
### General trends in california

In [4]:
population_df = pd.read_csv('./Data/Population_california.csv',sep=',')
wu = pd.read_csv('./Data/water_use.csv')
# convert to gallons

wu['Urban Water Use (MGal/year)'] = wu['Urban Water Use (maf/year)']*325851
historical_trends = pd.DataFrame({'Year':[2005,2030],'Urban Water Use (MGal/year)':[2948951.55,3909852]})


In [5]:
#TOOLS = "pan,wheel_zoom,box_zoom,reset,save"
keys = ['Year','Population']
fig = figure(title='Population CA & Water usage vs Year', tools=TOOLS, toolbar_location='left', 
              height=600,width=1000)
#fig.circle(comp_df[keys[0]],comp_df[keys[1]],size=6,alpha=0.5)
population_df.query('Year >= 1970',inplace=True)
x = population_df[keys[0]]
y = population_df[keys[1]]

fig.line(x,y,color='RoyalBlue', line_alpha=0.8, line_width=2)
fig.yaxis.axis_label = 'Population'+' (Millions)'
fig.yaxis.axis_label_text_color = 'RoyalBlue'


# Setting the second y axis range name and range
fig.extra_y_ranges = {"Water Usage": Range1d(start=0, end=4E6)}

# Adding the second axis to the plot.  
fig.add_layout(LinearAxis(y_range_name="Water Usage", axis_label="Water usage (MGal)", axis_label_text_color='green'), 'right')

keys = ['Year','Urban Water Use (MGal/year)']
#fig.circle(comp_df[keys[0]],comp_df[keys[1]],size=6,alpha=0.5)

x = wu[keys[0]]
y = wu[keys[1]]
fig.line(x, y, color="green", y_range_name="Water Usage",line_width=2)

x = historical_trends['Year']
y = historical_trends['Urban Water Use (MGal/year)']
fig.line(x, y, color="green", y_range_name="Water Usage",line_width=2,line_dash='dashed')

x_threshold_ln = Span(location=8.82*325851,dimension='width', line_color='red',
                      line_dash='dashed', line_width=1,y_range_name="Water Usage")
fig.add_layout(x_threshold_ln)


fig.xaxis.axis_label = 'Year'

fig.yaxis.major_label_text_font_size = '12pt'
fig.xaxis.major_label_text_font_size = '12pt'
fig.yaxis.axis_label_text_font_size = '14pt'
fig.xaxis.axis_label_text_font_size = '14pt'
fig.x_range = Range1d(1970,2030)

text = Label(x=650, y=400, text='Prediction water supply by 2030',
               x_units='screen', y_units='screen',text_font_size='12pt',text_color='Red')

dt_source_label = 'Data source: http://www.pacinst.org/app/uploads/2013/02/ca_water_20303.pdf'
dt_source_label2 ='http://www.waterboards.ca.gov/water_issues/programs/conservation_portal/'   

text_label = Label(x=130, y=110, text=dt_source_label,
               x_units='screen', y_units='screen',text_font_size='10pt',text_color='grey')
text_label2 = Label(x=130, y=90, text=dt_source_label2,
               x_units='screen', y_units='screen',text_font_size='10pt',text_color='grey')


fig.add_layout(text)
fig.add_layout(text_label)
fig.add_layout(text_label2)
show(fig)

## Load and pre-process Waterboards Dataset 

In [6]:
# Dataset locations

Pre_processed_dset_pth = './Data/Pre_processed_WU_dataset.csv'
DFT_PTH = './Data/hydrologic_regions_vs_counties.csv'
County_bounday_pth = './Data/counties_boundaries.hdf'


In [7]:
print('Downloading preprocessed dataset from:',Pre_processed_dset_pth)
df = pd.read_csv(Pre_processed_dset_pth)
print('Downloading county boundary data from:',County_bounday_pth)
#urllib.request.urlretrieve(County_bounday_pth,'counties_boundaries.hdf')
location_df = pd.read_hdf('./Data/counties_boundaries.hdf')
df.head(2)

Hydrologic Region                                Utility Stage Invoked  \
0  San Francisco Bay  East Bay Municipal Utilities District             0   
1  San Francisco Bay  East Bay Municipal Utilities District             0   

         Date  Population Mandatory Restrictions    Production  \
0  2017-01-15     1390000                     No  3.747100e+09   
1  2016-12-15     1400000                     No  3.767400e+09   

   Production 2013  Conservation target  % Residential       GPCD  \
0     4.099300e+09                  0.0           62.0  53.915108   
1     4.772000e+09                  0.0           62.0  53.820000   

   Days allowed per week  Complaints  Warnings  Penalties  \
0                    7.0          97         1          0   
1                    7.0           0         0          0   

   Penalties Assessment Rate  Utility_name  Year Month Type   County City  
0                          0  East Bay MUD  2017   Jan  NaN  Alameda  NaN  
1                          0  East Bay MUD  2016   Dec  NaN  Alameda  NaN

### Parse datetime

In [8]:

df['Date'] = pd.to_datetime(df.Date)
df['Date'] = df.Date.apply(lambda x: x.date())
#df['Date'] = df.Date.apply(lambda x:x.strftime("%Y-%m"))
df['Year']=df.Date.apply(lambda x: x.year)
df['Month']=df.Date.apply(lambda x: x.strftime('%b'))
df['monthcode']=df.Date.apply(lambda x: x.month)

df['Prod_res'] = df['Production']*df['% Residential']*0.01
df['Prod_ind_ag'] = df['Production']-df['Prod_res']

In [9]:
df['Conservation target'] = df['Conservation target']*100
df['Res_GPCD']=  df['GPCD']*df['% Residential']/100
df['Other_GPCD']=  df['GPCD']*(100-df['% Residential'])/100
df['Mandatory'] = df['Mandatory Restrictions'].replace(['Yes', 'No'], [1, 0])

#### 2013 production data is in another column: Stack production data in one column --> Stack them altogether


In [10]:

initcols = ['Utility_name','County','Hydrologic Region','Year','Month','% Residential']
subdf_1 = df[initcols+['Production' ]]
subdf_2 = df[initcols+['Production 2013' ]]
subdf_2.rename(columns = {'Production 2013':'Production'},inplace=True)
subdf_2['Year'] = 2013
subdf = pd.concat([subdf_1,subdf_2])
subdf['Date'] = subdf.Year.astype('str')+'-'+subdf.Month
subdf['datetime'] = pd.to_datetime(subdf['Date'])
subdf['Date'] = subdf.datetime.apply(lambda x:x.strftime("%Y-%m"))

subdf['Prod_res'] = subdf['Production']*subdf['% Residential']*0.01
subdf['Prod_ind_ag'] = subdf['Production']-subdf['Prod_res']
subdf.head(3)

Utility_name   County  Hydrologic Region  Year Month  % Residential  \
0  East Bay MUD  Alameda  San Francisco Bay  2017   Jan           62.0   
1  East Bay MUD  Alameda  San Francisco Bay  2016   Dec           62.0   
2  East Bay MUD  Alameda  San Francisco Bay  2016   Nov           61.0   

     Production     Date   datetime      Prod_res   Prod_ind_ag  
0  3.747100e+09  2017-01 2017-01-01  2.323202e+09  1.423898e+09  
1  3.767400e+09  2016-12 2016-12-01  2.335788e+09  1.431612e+09  
2  3.839100e+09  2016-11 2016-11-01  2.341851e+09  1.497249e+09

### Production/Use over time

In [11]:
f = subdf.groupby(['Hydrologic Region','Date']).agg('mean').reset_index()


#palette('Viridis6')
src = ColumnDataSource(f)
tools=[HoverTool()]
p1 = Bar(src.data,'Date', values='Production', title="Total Production/Water usage vs Date by Region",agg='sum', 
        stack = 'Hydrologic Region', width=800, height=500, palette = Viridis6,tools=TOOLS)
p1.legend.location = 'top_right'
p1.legend.background_fill_alpha = 0.7
show(p1)

In [13]:
key = 'Production'
avg_gp = mh.process_stats_by_counties(df,key=key,groupkey='monthcode',aggfunc='mean',srcpath=DFT_PTH)

#location_df = pd.read_hdf('./Challenge/water_flask/data/counties_boundaries.hdf')
location_df = pd.read_hdf('./Data/counties_boundaries.hdf')
location_df.query('State == "CA"',inplace=True)
data2 = avg_gp.merge(location_df,on='County',how='left')

cal_fig = mh.interactive_county_map(data2,key=key,slider_key='monthcode',initial_query='monthcode == 1',
                             title='Water usage averaged per Month by County'.format(key),
                             tools = "pan,wheel_zoom,box_zoom,reset,hover,save",
                             width=600,height=600)
show(cal_fig)

## Water savings per Year comparison DataFrame

### Savings per County

In [14]:
# Helper function to calulate savings

def calculate_savings(subdf,df,key='Production',groupby=['Hydrologic Region', 'County','Utility_name','Year']):
    # Year 2014 and 2017 data is incomplete let's drop them
    #let's calculate savings from 2013 to 2016
    #tmp = subdf.query('Year != 2014 & Year != 2017')

    prod_df = subdf.groupby(groupby)[key].agg(np.mean)
    # Year 2014 and 2017 data is incomplete let's drop them

    prod_df = prod_df.unstack(['Year'])
    prod_df.columns = ['Production_{}'.format(k) for k in prod_df.columns ]
    prod_df = prod_df.reset_index()

    tmp = df
    tmp = tmp.groupby(groupby)[['Conservation target','Mandatory']].agg(np.mean)
    tmp0 = tmp.unstack(['Year'])['Conservation target']
    tmp1 = tmp.unstack(['Year'])['Mandatory']
    tmp0.columns = ['Target_{}'.format(k) for k in tmp0.columns ]
    tmp1.columns = ['Mendatory_coeff_{}'.format(k) for k in tmp1.columns ]
    tmp0 = tmp0.fillna(0)
    tmp1 = tmp1.fillna(0)
    tmp = pd.concat([tmp0,tmp1],axis=1)
    tmp = tmp.reset_index()
    tmp['Cumulative_Target'] = 1
    
    for k in [2014,2015,2016,2017]:
        tmp['Cumulative_Target']=tmp['Cumulative_Target']*(1-tmp['Target_{}'.format(k)]*0.01)
    tmp['Cumulative_Target'] = (1-tmp['Cumulative_Target'])*100

    comp_df = pd.merge(prod_df,tmp,on=['Hydrologic Region', 'County','Utility_name'],how='outer')
    comp_df['Savings 2013-2014'] = (comp_df.Production_2014-comp_df.Production_2013)/comp_df.Production_2013*100
    comp_df['Savings 2014-2015'] = (comp_df.Production_2015-comp_df.Production_2014)/comp_df.Production_2014*100
    comp_df['Savings 2015-2016'] = (comp_df.Production_2015-comp_df.Production_2016)/comp_df.Production_2015*100
    comp_df['Savings 2013-2016'] = (comp_df.Production_2013-comp_df.Production_2016)/comp_df.Production_2013*100
    #comp_df = comp_df[[k for k in comp_df.columns if 'Production' not in k]]
    #comp_df.head(3)
    return comp_df

In [15]:
## Helper Plotting Functions

def horiz_cat_barplot(dfm,keys=['Savings','Utility'],extra_key = None,
                      title='',xrange=[0,100],invert_yrange=False,color='red',axis_location="left",
                      height=500,width=500,units=''):
    factors = list(dfm[keys[1]])
    xval = dfm[keys[0]]
    
    yrange = factors
    if invert_yrange:
        yrange = factors[::-1]
    
    fig = figure(title=title, tools="", toolbar_location=None,
                y_range=yrange, x_range=xrange,y_axis_location=axis_location,height=height,width=width)

    fig.rect(xval/2, factors, width=xval, height=0.7, color=color,alpha=0.7)
    
    if extra_key:
        x = dfm[extra_key]
        fig.circle(x, factors, size=2, fill_color="orange", line_width=3, alpha=0.5)
    fig.xaxis.major_label_text_font_size = '10pt'
    fig.yaxis.major_label_text_font_size = '10pt'
    fig.yaxis.major_label_text_font_size = '10pt'
    fig.xaxis.axis_label = keys[0]+units
    return fig

def best_worst_barplot(dfm,keys=['Savings','Utility'],extra_key = None,numrecords=20,
                       title='',xrange1=[0,30],xrange2=[0,30],invert_yrange=False,invert_xrange=False,color='red',
                       axis_location="left",units='',height=500,width=500):
    
    comp_df_sorted = dfm.dropna(subset=[keys[0]]).sort_values(by=keys[0],ascending=True)
    worst_dfm = comp_df_sorted.head(numrecords)
    
    
    fig1 = horiz_cat_barplot(worst_dfm,keys=keys,
                             extra_key = None,title='Worst {}'.format(keys[0]),xrange=xrange1,
                             invert_yrange=True,units=units,height=height,width=width)

    
    best_dfm = comp_df_sorted.tail(numrecords)
    fig2 = horiz_cat_barplot(best_dfm,keys=keys,
                             extra_key = None,title='Best {}'.format(keys[0]),color='DarkGreen',
                             axis_location="right",xrange=xrange2,units=units,height=height,width=width)
    return row(fig1,fig2)
    
    


In [16]:
comp_df = calculate_savings(subdf,df,key='Prod_res')
comdf_counties = comp_df.groupby(['County']).mean().reset_index()
comdf_counties['Savings 2015-2016'] = (comdf_counties.Production_2015-comdf_counties.Production_2016)/comdf_counties.Production_2015*100
comdf_counties['Savings 2013-2016'] = (comdf_counties.Production_2013-comdf_counties.Production_2016)/comdf_counties.Production_2013*100
comdf_counties = comdf_counties.dropna()
comdf_counties.head()

County  Production_2013  Production_2014  Production_2015  \
0    Alameda     8.167219e+08     7.459017e+08     6.050935e+08   
1     Amador     6.284719e+07     6.568831e+07     4.252763e+07   
2      Butte     1.816770e+08     1.777523e+08     1.211547e+08   
3  Calaveras     9.836650e+07     1.005362e+08     6.794636e+07   
4  Coastside     3.379741e+07     3.328649e+07     2.760585e+07   

   Production_2016  Production_2017  Target_2014  Target_2015  Target_2016  \
0     6.229169e+08     5.096168e+08          0.0    17.142857     6.928571   
1     4.662816e+07     2.785716e+07          0.0    24.000000     9.250000   
2     1.247822e+08     7.197844e+07          0.0    31.200000    12.509091   
3     7.487007e+07     3.532581e+07          0.0    16.000000     5.916667   
4     2.689839e+07     1.955250e+07          0.0     8.000000     3.333333   

   Target_2017  Mendatory_coeff_2014  Mendatory_coeff_2015  \
0          0.0              0.918367              1.000000   
1          0.0              1.000000              1.000000   
2          0.0              0.685714              0.966667   
3          0.0              1.000000              0.916667   
4          0.0              1.000000              1.000000   

   Mendatory_coeff_2016  Mendatory_coeff_2017  Cumulative_Target  \
0              0.750000              0.571429          22.766190   
1              0.416667              0.000000          31.030000   
2              0.981818              0.800000          39.703152   
3              0.833333              1.000000          20.970000   
4              0.916667              1.000000          11.066667   

   Savings 2013-2014  Savings 2014-2015  Savings 2015-2016  Savings 2013-2016  
0         -17.067879         -16.918257          -2.945557          23.729617  
1           4.520672         -35.258458          -9.642038          25.807102  
2          -2.635740         -30.445125          -2.994092          31.316434  
3           2.205726         -32.416028         -10.189973          23.886618  
4          -1.511714         -17.065903           2.562720          20.412869

In [17]:
fig = best_worst_barplot(comdf_counties,keys=['Savings 2015-2016','County'],extra_key = None,numrecords=15,
                         title='',xrange1=[-30,0],xrange2=[0,30],invert_yrange=False,invert_xrange=False,
                         color='red',axis_location="left",units=' (%)',width=400)
hover = fig.children[0].select(dict(type=HoverTool))
show(fig)

In [18]:
fig = best_worst_barplot(comdf_counties,keys=['Savings 2013-2016','County'],extra_key = None,numrecords=15,
                      title='',xrange1=[40,0],xrange2=[0,40],invert_yrange=True,color='red',axis_location="left",units=' (%)',width=400)
hover = fig.children[0].select(dict(type=HoverTool))
show(fig)

In [19]:


# Fill in missing values by averaging by hydrologic region
#test = comdf_counties
#key='Savings 2013-2016'
#test[key] = test.groupby(['Hydrologic Region']).transform(lambda x: x.fillna(x.mean()))
#grouped_df.groupby(['County',groupkey])[key].agg(aggfunc).reset_index()

p = simple_county_map(comdf_counties,key='Savings 2013-2016',width=600,height=600,palette=Viridis256[::-1],
                      state='ca',
                      title='California Water Savings from 2013-2016',
                      tools="pan,wheel_zoom,box_zoom,reset,hover,save",
                      color_range=[0,40])
show(p)

### Correlation of Savings with Savings Targets

In [20]:

def plot_fit(fig,dfm,keys=['Target_2016','Savings 2015-2016'],color='RoyalBlue'):
    x = np.array(dfm[keys[0]])
    y = np.array(dfm[keys[1]])
    X = sm.add_constant(x)


    result = sm.OLS(y, X).fit()
    st, data, ss2 = summary_table(result, alpha=0.05)
    fittedvalues = data[:,2]
    # confidence intervals
    #predict_mean_ci_low, predict_mean_ci_upp = data[:,4:6].T
    #predict_ci_low, predict_ci_upp = data[:,6:8].T

    fig.line(x,fittedvalues,color=color, line_alpha=0.8, line_width=2,legend='linear fit')

    #print(st)
    #nx = np.hstack([x,np.flipud(x)])
    #ny = np.hstack([predict_mean_ci_low,np.flipud(predict_mean_ci_upp)])
    #fig.patch(nx,ny,color='blue',alpha=0.2)

    #nx = np.hstack([x,np.flipud(x)])
    #ny = np.hstack([predict_ci_low,np.flipud(predict_ci_upp)])
    #fig.patch(nx,ny,color='blue',alpha=0.05)
    return result

### Correlation with Residential water usage

In [21]:
keys = ['Cumulative_Target','Savings 2013-2016']
fig = figure(title='Savings vs Targets', tools=TOOLS, toolbar_location='left', 
              height=600,width=800)

comp_df = calculate_savings(subdf,df,key='Prod_res')
corr = np.corrcoef(comp_df[keys[0]],comp_df[keys[1]])[0,1]
fig.circle(comp_df[keys[0]],comp_df[keys[1]],size=6,alpha=0.3,color='blue',legend='Prod_res')


r1 = plot_fit(fig,comp_df,keys=keys,color='RoyalBlue')

fig.xaxis.axis_label = 'Cumulative Savings vs  (%)'
fig.yaxis.axis_label = keys[1]+' (%)'
fig.yaxis.major_label_text_font_size = '14pt'
fig.xaxis.major_label_text_font_size = '14pt'
fig.yaxis.axis_label_text_font_size = '12pt'
fig.xaxis.axis_label_text_font_size = '12pt'
fig.y_range = Range1d(0,100)

lbl_text = Label(x=650, y=500, text='Correlation coeff {:.2f}'.format(corr),
               x_units='screen', y_units='screen',text_font_size='10pt')

fig.add_layout(lbl_text)


fig.legend.location = "top_left"
show(fig)

### Targets vs industrial and residential water usage

In [22]:
keys = ['Cumulative_Target','Savings 2013-2016']
fig = figure(title='Savings vs Targets', tools=TOOLS, toolbar_location='left', 
              height=600,width=800)

comp_df = calculate_savings(subdf,df,key='Prod_res')
corr = np.corrcoef(comp_df[keys[0]],comp_df[keys[1]])[0,1]
fig.circle(comp_df[keys[0]],comp_df[keys[1]],size=6,alpha=0.3,color='blue',legend='Prod_res')

comp_df2 = calculate_savings(subdf,df,key='Prod_ind_ag')
comp_df2 = comp_df2.dropna()
corr2 = np.corrcoef(comp_df2[keys[0]],comp_df2[keys[1]])[0,1]
fig.circle(comp_df2[keys[0]],comp_df2[keys[1]],size=6,alpha=0.3,color='red',legend='Prod_industrial_ag')

r1 = plot_fit(fig,comp_df,keys=keys,color='RoyalBlue')
r2 = plot_fit(fig,comp_df2,keys=keys,color='red')

fig.xaxis.axis_label = 'Cumulative Savings Target (%)'
fig.yaxis.axis_label = keys[1]+' (%)'
fig.yaxis.major_label_text_font_size = '14pt'
fig.xaxis.major_label_text_font_size = '14pt'
fig.yaxis.axis_label_text_font_size = '12pt'
fig.xaxis.axis_label_text_font_size = '12pt'
fig.y_range = Range1d(0,100)

lbl_text = Label(x=650, y=500, text='Correlation coeff {:.2f}'.format(corr),
               x_units='screen', y_units='screen',text_font_size='10pt')
lbl_text2 = Label(x=650, y=450, text='Correlation coeff {:.2f}'.format(corr2),
               x_units='screen', y_units='screen',text_font_size='10pt')

fig.add_layout(lbl_text)
fig.add_layout(lbl_text2)

fig.legend.location = "top_left"
#fig.legend.click_policy="hide"

#output_file("interactive_legend.html", title="interactive_legend.py example")

show(fig)

### Significance test  both fits

In [23]:
sumr = r1.summary()
#sumr.tables[0]
sumr.tables[0]

<class 'statsmodels.iolib.table.SimpleTable'>

In [24]:
sumr = r2.summary()
sumr.tables[0]
#sumr.tables[1]

<class 'statsmodels.iolib.table.SimpleTable'>

### Correlation matrix

In [25]:
def plot_correlation_matrix(dfm,threshold=0,width=600,heigth=600):
    corrm = dfm.corr().unstack().reset_index()
    cols = [k for k in corrm.columns]
    corrm['absval'] = corrm[0].abs()
    if threshold:
        corrm = corrm.query('absval >= {} & absval < 0.997'.format(threshold))
    #print(corrm)
    corrm = corrm[cols]
    factors = list(corrm.level_0.unique())
    corrm.columns = ['lv0','lv1','corr']

    TOOLS = "hover"
    fig = HeatMap(corrm, x='lv0', y='lv1', values='corr', stat=None, 
                  width=width, plot_height=heigth,tools=TOOLS, 
                  palette = RdYlGn10)
    fig.x_range.factors = fig.x_range.factors[::-1]
    hover = fig.select(dict(type=HoverTool))
    hover.tooltips = [
        ("x", "@x"),
        ("y", "@y"),
        ("Correlation", "@values"),
    ]
    fig.legend.location = None
    fig.above
    fig.title.text = 'Correlation matrix'
    fig.xaxis.major_label_text_font_size ='12pt'
    fig.yaxis.major_label_text_font_size ='12pt'
    fig.xaxis.axis_label =''
    fig.yaxis.axis_label =''
    return fig

In [26]:
comp = comp_df[[k for k in comp_df.columns if 'Production' not in k]]
fig = plot_correlation_matrix(comp,width=800,heigth=800)
show(fig)

## Predictive Modeling for total production/Region/Year
### Using linear regression with regularization (Poly features)

In [27]:
from scipy.stats import skew
from sklearn.preprocessing import PolynomialFeatures
from sklearn.model_selection import train_test_split
from sklearn.linear_model import Ridge, RidgeCV, ElasticNet, LassoCV, LassoLarsCV
from sklearn.model_selection import cross_val_score
from sklearn.metrics import mean_squared_error

In [28]:
# Feature Selection
X_ = df[['monthcode','Year']]
dummies = pd.get_dummies(df['Hydrologic Region'])

# Let's encode the regions
X = pd.concat([X_,dummies],axis=1)
y =np.log(df['Production']) ## To Deskew the distribution of production


In [29]:

alphas = 10**np.linspace(8,-5,25)*0.5

model = Ridge(normalize=True)

coefs = []
errorlist = []

parameter_list = []

Degree = [1,2,3,4]
for i in Degree:
    
    polynomial_features = PolynomialFeatures(degree=i,include_bias=False)
    scaled_X = polynomial_features.fit_transform(X)
    X_train, X_test, y_train, y_test = train_test_split(scaled_X, y, test_size=0.33, random_state=40)
      
    for a in alphas:

        

        model.set_params(alpha=a)
        model.fit(X_train, y_train)
        
        # Cross validation error
        y_predicted = model.predict(X_test)
        error= mean_squared_error(y_test, y_predicted)
        
        entry = {'Degree':i, 'Alpha':a,'MSE':error, 'Coefficients':model.coef_}
        parameter_list.append(entry)
        
parameters = pd.DataFrame(parameter_list)[['Degree','Alpha','MSE','Coefficients']]

### Let's plot the cross validation error 
#### for different values of reg param alpha and polynomial degree

In [30]:
p = figure(width=600,height=400,y_axis_type="log",x_axis_type="log",
           title='CV Mean Square Error vs Regularization param by degree',
           tools="hover,pan,box_zoom,reset")
colors = ['blue','red','green','orange','grey']

for i,(degree,gp) in enumerate(parameters.groupby('Degree')):
    p.line(gp.Alpha,gp.MSE, line_width=2,line_color=colors[i],legend="Degree: {}".format(degree))
    p.circle(gp.Alpha,gp.MSE, line_width=2,line_color=colors[i])
p.xaxis.axis_label = 'alpha'
p.yaxis.axis_label = 'Mean square error'
hover = p.select(dict(type=HoverTool))
hover.tooltips = [
    ("Alpha", "@x"),
    ("MSE", "@y"),
]
p.legend.location = 'top_left'
show(p)

### Example let's plot the data for 2016 for San Francisco Bay and compre with predictions
#### First Train model

In [31]:
# Train the model with "optimal alpha and degree" and model set to ridge
polynomial_features = PolynomialFeatures(degree=4,include_bias=False)
scaled_X = polynomial_features.fit_transform(X)
model.set_params(alpha=8E-3)
model.fit(scaled_X, y)
y_predicted = model.predict(scaled_X)
error= mean_squared_error(y, y_predicted)
print('error:',error)

error: 1.0263202434


In [32]:
#Build vecor of features
Location = 'San Francisco Bay'
Tgt_Year = 2015


dt = X[(X[Location] == 1) & (X['Year'] == 2015)]
dt = dt.head(12)
dt['Year'] = Tgt_Year
dt['monthcode'] = [1,2,3,4,5,6,7,8,9,10,11,12]

scaled_dt = polynomial_features.fit_transform(dt)
log_y_predicted = model.predict(scaled_dt)

y_predicted = np.exp(log_y_predicted)

In [34]:

#Build vecor of features
Location = 'San Francisco Bay'
Tgt_Year = 2016


dt = X[(X[Location] == 1) & (X['Year'] == Tgt_Year)]
dt = dt.head(12)
dt['Year'] = Tgt_Year
dt['monthcode'] = [1,2,3,4,5,6,7,8,9,10,11,12]

scaled_dt = polynomial_features.fit_transform(dt)
log_y_predicted = model.predict(scaled_dt)

y_predicted = np.exp(log_y_predicted)

log_data = y[(X[Location] == 1) & (X['Year'] == Tgt_Year)]
data = np.exp(log_data)

mean = data.mean()
std = data.std()
p = figure(width=800,height=500,
           title='Predicted production vs month for {} for the {} region'.format(Tgt_Year,Location),
           tools="hover,pan,box_zoom,reset,save",y_range=[mean-std,mean+std])
p.line(dt['monthcode'],y_predicted, line_width=2,line_color='red',legend="Model")
p.circle(X['monthcode'],data, size=2,color='grey',legend="Data")
p.legend.location = 'top_left'
p.xaxis.axis_label = 'Month'
p.xaxis.axis_label = 'Month'
p.yaxis.axis_label = 'Prdoduction (MGal)'
p.y_range = Range1d(0,4E8)
show(p)

#### Plot for other regions

In [35]:
Tgt_Year = 2016

In [36]:
Locations = [k for k in df['Hydrologic Region'].unique()]
palette = ['grey', 'red', 'green', 'blue', 'orange','DarkBlue','DarkViolet','Black']

In [37]:

p = figure(width=800,height=500,
               title='Predicted production vs month for {} for various CA regions'.format(Tgt_Year,Location),
               tools="hover,pan,box_zoom,reset,save",y_range=[mean-std,mean+std])
colors = palette
for i,Location in enumerate(Locations[0:8]):
#Build vecor of features


    dt = X[(X[Location] == 1) & (X['Year'] == Tgt_Year)]
    dt = dt.head(12)
    dt['Year'] = Tgt_Year
    dt['monthcode'] = [1,2,3,4,5,6,7,8,9,10,11,12]

    scaled_dt = polynomial_features.fit_transform(dt)
    log_y_predicted = model.predict(scaled_dt)

    y_predicted = np.exp(log_y_predicted)

    log_data = y[(X[Location] == 1) & (X['Year'] == Tgt_Year)]
    data = np.exp(log_data)

    mean = data.mean()
    std = data.std()
    p.line(dt['monthcode'],y_predicted, line_width=2,line_color=colors[i],legend="{}".format(Location))
    p.circle(X['monthcode'],data, size=2,color=colors[i],alpha=0.2)

p.legend.location = 'top_left'
p.legend.background_fill_alpha = 0.2
p.xaxis.axis_label = 'Month'
p.yaxis.axis_label = 'Usage (MGal)'
p.yaxis.major_label_text_font_size = '12pt'
p.xaxis.major_label_text_font_size = '12pt'
p.xaxis.axis_label_text_font_size = '12pt'
p.yaxis.axis_label_text_font_size = '12pt'
p.y_range = Range1d(0,4E8)
show(p)